# PseudoDojo notebook for Rh-sp

In [ ]:
from __future__ import print_function, division, unicode_literals
#import seaborn
%matplotlib inline

In [ ]:
from IPython.display import HTML
HTML('''
<style>
body {
background-image: url('http://www.pseudo-dojo.org/img/pw_maze_white.png');
}
</style>
<script>
code_show=true;
function code_toggle() {
 if (code_show) {
    $('div.input').hide();
 } else {
    $('div.input').show();
 }
 code_show = !code_show;
}
$(document).ready(code_toggle);
</script>
The raw code for this IPython notebook is by default hidden for easier reading.
To toggle on/off the raw code, click <a href="javascript:code_toggle()">here</a>.''')

In [ ]:
from pseudo_dojo.core.pseudos import dojopseudo_from_file
pseudo = dojopseudo_from_file('/Users/setten/software/conda_install/setten_stack/pseudo_dojo/pseudo_dojo/pseudos/website/nc-sr_pbe_stringent/Rh-sp.psp8')
report = pseudo.dojo_report

## ONCVPSP Input File

In [ ]:
input_file = pseudo.filepath.replace(".psp8", ".in")
%cat $input_file

In [ ]:
# Get data from the oncvpsp output file
from pseudo_dojo.ppcodes.oncvpsp import OncvOutputParser, PseudoGenDataPlotter
onc_parser = OncvOutputParser(pseudo.filepath.replace(".psp8", ".out"))

# Parse the file and build the plotter
onc_parser.scan()
plotter = onc_parser.make_plotter()

## AE and PS radial wavefunctions $\phi(r)$

In [ ]:
fig = plotter.plot_radial_wfs()

## Arctan of the logarithmic derivatives

From the oncvpsp documentation:
The plots show $\phi(E) = \arctan(R * d \psi(r)/dr |_R)$ for some $R$
greater than the core radius, where $\psi$ is the solution of the non-local
radial equation regular at the origin (i.e., the outward-integrated solution).
For a well-designed pseudopotential, $\phi(E)$ will closely track that of the all-electron potential
over a wide range of energies from well-below to well-above the valence semi-core states of interest.
The steps of $\pi$ indicate localized pseudo wave functions.
Spurious steps of $\pi$ indicate "ghost" states, which are localized states than on investigation
turn out to have more nodes than appropriate for their energies.

For $GW$ pseudos, no significant deviation should be present up to 8 Hartree.

In [ ]:
fig = plotter.plot_atan_logders()

## Convergence in $G$-space estimated by ONCVPSP
These results are obtained in the atomic configuration and should give a reasonable estimate
of the convergence behaviour wrt to `ecut` in crystalline systems.

In [ ]:
fig = plotter.plot_ene_vs_ecut()

## Projectors

In general the second projector in any channel should have one node more that the first one.
Pushing the energy of the second projector too high may cause an additional node.
This will most likely introduce ghosts.

In [ ]:
fig = plotter.plot_projectors()

## Core-Valence-Model charge densities

Much better convergence properties can been achieved with `icmod 3`.
In this case, `fcfact` mainly determines the height of the model core charge while
`rcfact` mainly determines the width of the model core charge.

In [ ]:
fig = plotter.plot_densities()

## Local potential and $l$-dependent potentials

In [ ]:
fig = plotter.plot_potentials()

## Ghosts Test

Self-consistent band structure calculation performed on a regular mesh.
The algorithm to detect ghosts is just an indication usually on the side of false positives.
Zoom in on the band plot to see if an actual ghost is there.

In [ ]:
fig = report.plot_ebands(with_soc=False)

## Convergence of the total energy wrt ecut
The energies are obtained from the deltafactor calculations performed at the Wien2K equilibrium volume

In [ ]:
fig = report.plot_etotal_vs_ecut()

In [ ]:
fig = report.plot_etotal_vs_ecut(inv_ecut=True)

## Convergence of the Delta-Gauge results

The Delta-gauge compares the Equation Of State (EOS) of the elemental solid of the element calculated using the pseudo
potential to reference curves calculated using an all electron method. The Delta-gauge was introduced by K. Lejaeghere,
V. Van Speybroeck, G. Van Oost, and&S. Cottenier in [Critical Reviews in Solid State and Materials Sciences 39, 1](http://www.tandfonline.com/doi/abs/10.1080/10408436.2013.772503)

A comparison using the Delta-gauge between many codes and many pseudo tables can be found at the
[center for molecular modeling](http://molmod.ugent.be/deltacodesdft) and in
[Science 351, 1394-1395](http://science.sciencemag.org/content/351/6280/aad3000.full?ijkey=teUZMpwU49vhY&keytype=ref&siteid=sci)


In [ ]:
fig = report.plot_deltafactor_convergence(xc=pseudo.xc, what=("dfact_meV", "dfactprime_meV"))

## Convergence of $\Delta v_0$, $\Delta b_0$, and $\Delta b_1$ (deltafactor tests)

In [ ]:
# Absolute difference with respect to Wien2k results.
fig = report.plot_deltafactor_convergence(xc=pseudo.xc, what=("-dfact_meV", "-dfactprime_meV"))

## Delta-gauge EOS for the different cutoff energies

In [ ]:
fig = report.plot_deltafactor_eos()

## Convergence of the GBRV lattice parameters

The GBRV tests compare the lattice parameter of a FCC and BCC lattice of the element to all electron reference
data. The test was introduced by Kevin F. Garrity, Joseph W. Bennett, Karin M. Rabe, and David Vanderbilt in
developing th GBRV pseudo potential table. More information can be found in [Computational Materials Science 81,
446-452.](http://www.sciencedirect.com/science/article/pii/S0927025613005077)


In [ ]:
fig = report.plot_gbrv_convergence()

## Convergence of the phonon frequencies at $\Gamma$
The calculation is performed with the Wien2k relaxed parameters obtained from the deltafactor CIF files.


In [ ]:
fig = report.plot_phonon_convergence()

## GBRV EOS for the FCC structure

In [ ]:
fig = report.plot_gbrv_eos(struct_type="fcc")

## GBRV EOS for the BCC structure

In [ ]:
fig = report.plot_gbrv_eos(struct_type="bcc")

## Convergence of rocksalt lattice parameter.

In [ ]:
fig = report.plot_raren_convergence(pseudo.xc)